In [1]:
import re
from pymongo import MongoClient
import pandas as pd
import nltk
from nltk.probability import FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
import string

In [2]:
# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data'] 
raw_collection = db['01. raw_data_ajaib']   
prepo_collection = db['02. prepo_data_ajaib'] 

# Mengambil beberapa dokumen dari koleksi lama
data = raw_collection.find({})  # Misalnya, mengambil semua dokumen

# Menyimpan dokumen-dokumen tersebut ke dalam list
data_list = list(data)

# Menyimpan data ke dalam koleksi baru
prepo_collection.insert_many(data_list)


InsertManyResult([ObjectId('663862c1dd520c9ba22efdc2'), ObjectId('663862c1dd520c9ba22efdc3'), ObjectId('663862c1dd520c9ba22efdc4'), ObjectId('663862c1dd520c9ba22efdc5'), ObjectId('663862c1dd520c9ba22efdc6'), ObjectId('663862c1dd520c9ba22efdc7'), ObjectId('663862c1dd520c9ba22efdc8'), ObjectId('663862c1dd520c9ba22efdc9'), ObjectId('663862c1dd520c9ba22efdca'), ObjectId('663862c1dd520c9ba22efdcb'), ObjectId('663862c1dd520c9ba22efdcc'), ObjectId('663862c1dd520c9ba22efdcd'), ObjectId('663862c1dd520c9ba22efdce'), ObjectId('663862c1dd520c9ba22efdcf'), ObjectId('663862c1dd520c9ba22efdd0'), ObjectId('663862c1dd520c9ba22efdd1'), ObjectId('663862c1dd520c9ba22efdd2'), ObjectId('663862c1dd520c9ba22efdd3'), ObjectId('663862c1dd520c9ba22efdd4'), ObjectId('663862c1dd520c9ba22efdd5'), ObjectId('663862c1dd520c9ba22efdd6'), ObjectId('663862c1dd520c9ba22efdd7'), ObjectId('663862c1dd520c9ba22efdd8'), ObjectId('663862c1dd520c9ba22efdd9'), ObjectId('663862c1dd520c9ba22efdda'), ObjectId('663862c1dd520c9ba22efd

In [3]:
# Menghapus field yang tidak diperlukan
prepo_collection.update_many({}, {'$unset': {'reviewId': '', 'userName': '', 'userImage': '', 'score': '',
                                       'thumbsUpCount': '', 'reviewCreatedVersion': '','replyContent': '',
                                       'repliedAt': '', 'appVersion': ''}})

# Menampilkan data setelah penghapusan field
cursor = prepo_collection.find()
for document in cursor:
    print(document)

{'_id': ObjectId('663862c1dd520c9ba22efdc2'), 'content': 'Ga bisa verifikasi jelek', 'at': datetime.datetime(2024, 5, 5, 12, 11, 55)}
{'_id': ObjectId('663862c1dd520c9ba22efdc3'), 'content': 'Selalu gagal dalam tanda tangan. Coba ulangi foto KTP juga kembali ke foto KTP terus', 'at': datetime.datetime(2024, 5, 5, 7, 32, 30)}
{'_id': ObjectId('663862c1dd520c9ba22efdc4'), 'content': 'Lama banget selesai verifikasi nya sangat mengecewakan aplikasi burin', 'at': datetime.datetime(2024, 5, 5, 6, 58, 43)}
{'_id': ObjectId('663862c1dd520c9ba22efdc5'), 'content': 'Kenapa pas jual saham selalu ga bisa bisa ya', 'at': datetime.datetime(2024, 5, 4, 16, 24, 9)}
{'_id': ObjectId('663862c1dd520c9ba22efdc6'), 'content': 'Aplikasi gatau lagi gangguan gatau apa atau aku kurang update sisa penjualan saham aku ada sekitar 2-300k tapi kenapa pas barusan di cek sahamnya ilang dan diriwayat pembelian saham nya juga gaada, malah yg adanya cuma Reksadana 11k. Td nya mau mulai aktif lagi beli saham, tapi kok g

In [4]:
def count_changes(original_text, modified_text):
    count = sum(1 for i, j in zip(original_text, modified_text) if i != j)
    return count

def lowercase(text):
    modified_text = text.lower()
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

cursor = prepo_collection.find()

total_lower_count = 0

for document in cursor:
    review = document['content']
    lower_review, lower_count = lowercase(review)

# Memperbarui dokumen dengan review yang sudah bersih
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': lower_review}})

    total_lower_count += lower_count

# Menampilkan jumlah karakter non-ascii yang dihapus
print(f"Total jumlah huruf yang diubah menjadi huruf kecil: {total_lower_count}")


Total jumlah huruf yang diubah menjadi huruf kecil: 29766


In [5]:
def remove_ascii(text):
    modified_text = text.encode('ascii', 'replace').decode('ascii')
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

cursor = prepo_collection.find()

total_cleaned_count = 0

for document in cursor:
    review = document['content']
    cleaned_review, cleaned_count = remove_ascii(review)

    # Memperbarui dokumen dengan review yang sudah bersih
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah karakter non-ascii yang dihapus
print(f"Jumlah karakter non-ASCII yang dihapus: {total_cleaned_count}")


Jumlah karakter non-ASCII yang dihapus: 2348


In [6]:
def remove_punctuation(text):
    # Pola regex untuk tanda baca
    punctuation_pattern = r'[' + re.escape(string.punctuation) + ']'
    # [!"\#\$%\&'\(\)\*\+,\-\./:;<=>\?@\[\\\]\^_`\{\|\}\~]

    # Menghapus tanda baca menggunakan regex
    modified_text = re.sub(punctuation_pattern, '', text)
    changes_count = count_changes(text, modified_text)
    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_punctuation(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah tanda baca yang dihapus
print(f"Jumlah tanda baca yang dihapus: {total_cleaned_count}")


Jumlah tanda baca yang dihapus: 632331


In [7]:
def remove_number(text):
    modified_text = re.sub(r"\d+", " ", text)
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_number(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah angka yang dihapus
print(f"Jumlah angka yang dihapus: {total_cleaned_count}")

Jumlah angka yang dihapus: 72370


In [8]:
def remove_single_char(text):
    modified_text = re.sub(r"\b[a-zA-Z]\b", " ", text)
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = remove_single_char(review)
    
    # Memperbarui dokumen dengan review yang sudah bersih
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah karakter tunggal yang dihapus
print(f"Jumlah karakter tunggal yang dihapus: {total_cleaned_count}")


Jumlah karakter tunggal yang dihapus: 741


In [9]:
def normalize_whitespace(text):
    modified_text = re.sub(r'\s+', ' ', text).strip()
    
    changes_count = count_changes(text, modified_text)

    return modified_text, changes_count

# Mengambil semua dokumen dari koleksi
documents = prepo_collection.find()

total_cleaned_count = 0

for document in documents:
    review = document['content']
    cleaned_review, cleaned_count = normalize_whitespace(review)
    
    # Memperbarui dokumen dengan review yang sudah dibenarkan
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': cleaned_review}})

    total_cleaned_count += cleaned_count

# Menampilkan jumlah whitespace yang dihapus
print(f"Jumlah whitespace yang dihapus: {total_cleaned_count}")


Jumlah whitespace yang dihapus: 266792


In [10]:
import pandas as pd
import logging

# Konfigurasi logging
logging.basicConfig(filename='perubahan_normalisasi_ajaib.log', level=logging.INFO, format='%(asctime)s - %(message)s')

# Fungsi untuk membaca kamus dari file CSV dan mengembalikan kamus singkatan
def load_abbreviations(csv_file, delimiter=';'):
    df = pd.read_csv(csv_file, delimiter=delimiter)
    return dict(zip(df['before'], df['after']))

# Fungsi untuk memperluas singkatan dalam teks
def expand_abbreviations(text, abbreviations):
    expanded_tokens = []
    for word in text.split():
        expanded_word = abbreviations.get(word.lower(), word)
        if expanded_word != word:
            logging.info(f"Mengganti '{word}' menjadi '{expanded_word}'")
        expanded_tokens.append(expanded_word)
    expanded_text = ' '.join(expanded_tokens)
    return expanded_text

# Mengambil kamus singkatan dari file CSV
abbreviations = load_abbreviations('kamus_normalisasi.csv')

# Mendapatkan data dari koleksi MongoDB
documents = prepo_collection.find()

# Inisialisasi variabel untuk menyimpan total jumlah kata yang telah diperluas
total_expanded_count = 0

# Loop melalui setiap dokumen dalam koleksi
for document in documents:
    # Ambil teks review dari dokumen
    review = document['content']
    
    # Perluas singkatan dalam teks review
    expanded_review = expand_abbreviations(review, abbreviations)
    
    # Hitung perbedaan jumlah kata sebelum dan setelah perluasan
    expanded_count = len(expanded_review.split()) - len(review.split())

    # Memperbarui dokumen dengan review yang sudah diperluas
    prepo_collection.update_one({'_id': document['_id']}, {'$set': {'content': expanded_review}})

    # Menambahkan jumlah kata yang telah diperluas ke total_expanded_count
    total_expanded_count += expanded_count

# Menampilkan jumlah kata yang telah diperluas
print(f"Jumlah kata yang telah diperluas: {total_expanded_count}")


Jumlah kata yang telah diperluas: 650


In [11]:
def remove_duplicate_chars(text):
    words = text.split()
    cleaned_words = []
    changes_count = 0
    for word in words:
        cleaned_word = re.sub(r'(\w)\1+', r'\1', word)
        changes_count += count_changes(word, cleaned_word)
        cleaned_words.append(cleaned_word)
    
    cleaned_text = " ".join(cleaned_words)

    return cleaned_text, changes_count

# Mendapatkan data dari koleksi MongoDB
cursor = prepo_collection.find()

total_changes_count = 0

for document in cursor:
    review = document['content']
    
    # Menghapus karakter ganda dalam review
    cleaned_review, changes_count = remove_duplicate_chars(review)
    
    # Memperbarui field 'review' dengan review yang sudah dibersihkan
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'content': cleaned_review}}
    )

    total_changes_count += changes_count

# Menampilkan jumlah karakter ganda yang dihapus
print(f"Jumlah karakter ganda yang dihapus: {total_changes_count}")


Jumlah karakter ganda yang dihapus: 14959


In [12]:
# Mendapatkan data dari koleksi MongoDB
cursor = prepo_collection.find()

for document in cursor:
    review = document['content']
    
    # Melakukan tokenisasi menggunakan word_tokenize dari nltk
    tokens = word_tokenize(review)
    
    # Memperbarui field 'tokenized_review' dengan daftar token
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'tokenized_review': tokens}}
    )

    print(tokens)

['tidak', 'bisa', 'verifikasi', 'jelek']
['selalu', 'gagal', 'dalam', 'tanda', 'tangan', 'coba', 'ulangi', 'foto', 'ktp', 'juga', 'kembali', 'ke', 'foto', 'ktp', 'terus']
['lama', 'sangat', 'selesai', 'verifikasi', 'nya', 'sangat', 'mengecewakan', 'aplikasi', 'burik']
['kenapa', 'cocok', 'jual', 'saham', 'selalu', 'tidak', 'bisa', 'bisa', 'ya']
['aplikasi', 'tidak', 'tahu', 'lagi', 'ganguan', 'tidak', 'tahu', 'apa', 'atau', 'aku', 'kurang', 'baru', 'sisa', 'penjualan', 'saham', 'aku', 'ada', 'sekitar', 'tapi', 'kenapa', 'cocok', 'barusan', 'di', 'lihat', 'sahamnya', 'ilang', 'dan', 'diriwayat', 'pembelian', 'saham', 'nya', 'juga', 'tidak', 'ada', 'malah', 'yang', 'adanya', 'cuma', 'investasi', 'td', 'nya', 'mau', 'mulai', 'aktif', 'lagi', 'beli', 'saham', 'tapi', 'kok', 'gini', 'ya', 'tidak', 'ada', 'konfirmasi', 'tapi', 'tiba', 'saham', 'nya', 'ilang', 'mungkin', 'buat', 'sebagian', 'orang', 'uang', 'segitu', 'tidak', 'ada', 'artinya', 'kalo', 'buat', 'saya', 'uang', 'segitu', 'cukup'

In [13]:
import nltk
from nltk.corpus import stopwords
# Mendapatkan data dari koleksi MongoDB
cursor = prepo_collection.find()

# Mengambil daftar stopwords dalam bahasa Indonesia
list_stopwords = stopwords.words('indonesian')

list_stopwords.extend([
    "ny", 'klo', 'aah','ah','luu','we','wee','la','tah','kalo', 'biar', 'buat', 'bilang','bagaimana','cuma', 'karena', 'nya', 'nih', 'sih','at','gitu','tapi',
    'si', 'tau', 'tuh', 'untuk', 'ya', 'iya','mah','nder','jadi', 'sudah', 'saja','wah','ini','gw', 'hehe', 'pen','nan', 'loh', 'iii','wah','si','vi',
    'eee', 'setelah', 'tynyjunaz', 'ktol', 'yang', 'padahal', 'bagetikut', 'mu', 'loh', 'sih', 'tiba', 'tari', 'saja', 'ah',
    'kah', 'sekali', 'aju', 'hey', 'gini', 'halo', 'buk', 'si', 'hai', 'halo', 'min', 'lh', 'so', 'wae', 'jos', 'kalau', 'di', 'dh', 'dah',
    'ke', 'dom', 'juga', 'tiba', 'dari', 'ni', 'kak', 'mas', 'mba'
])
list_stopwords


['ada',
 'adalah',
 'adanya',
 'adapun',
 'agak',
 'agaknya',
 'agar',
 'akan',
 'akankah',
 'akhir',
 'akhiri',
 'akhirnya',
 'aku',
 'akulah',
 'amat',
 'amatlah',
 'anda',
 'andalah',
 'antar',
 'antara',
 'antaranya',
 'apa',
 'apaan',
 'apabila',
 'apakah',
 'apalagi',
 'apatah',
 'artinya',
 'asal',
 'asalkan',
 'atas',
 'atau',
 'ataukah',
 'ataupun',
 'awal',
 'awalnya',
 'bagai',
 'bagaikan',
 'bagaimana',
 'bagaimanakah',
 'bagaimanapun',
 'bagi',
 'bagian',
 'bahkan',
 'bahwa',
 'bahwasanya',
 'baik',
 'bakal',
 'bakalan',
 'balik',
 'banyak',
 'bapak',
 'baru',
 'bawah',
 'beberapa',
 'begini',
 'beginian',
 'beginikah',
 'beginilah',
 'begitu',
 'begitukah',
 'begitulah',
 'begitupun',
 'bekerja',
 'belakang',
 'belakangan',
 'belum',
 'belumlah',
 'benar',
 'benarkah',
 'benarlah',
 'berada',
 'berakhir',
 'berakhirlah',
 'berakhirnya',
 'berapa',
 'berapakah',
 'berapalah',
 'berapapun',
 'berarti',
 'berawal',
 'berbagai',
 'berdatangan',
 'beri',
 'berikan',
 'berikut'

In [14]:
list_stopwords = set(list_stopwords)

for document in cursor:
    review = document['tokenized_review']
    
    # Menghapus stopwords dari review menggunakan stopwords dalam bahasa Indonesia
    filtered_review = [word for word in review if word.lower() not in list_stopwords]
    
    # Memperbarui field 'filtered_review' dengan review yang sudah tidak mengandung stopwords
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'filtered_review': filtered_review}}
    )

    print (filtered_review)

['verifikasi', 'jelek']
['gagal', 'tanda', 'tangan', 'coba', 'ulangi', 'foto', 'ktp', 'foto', 'ktp']
['selesai', 'verifikasi', 'mengecewakan', 'aplikasi', 'burik']
['cocok', 'jual', 'saham']
['aplikasi', 'ganguan', 'sisa', 'penjualan', 'saham', 'cocok', 'barusan', 'lihat', 'sahamnya', 'ilang', 'diriwayat', 'pembelian', 'saham', 'investasi', 'td', 'aktif', 'beli', 'saham', 'konfirmasi', 'saham', 'ilang', 'orang', 'uang', 'segitu', 'uang', 'segitu', 'beli', 'kumpul', 'uang', 'kecewa', 'asli']
['tolong', 'diperbaiki', 'saham', 'hilang', 'pengembalian', 'dana']
['ruang', 'email', 'pengaduan', 'jam', 'kerja', 'mengkonfirmasi', 'deposit', 'rdn', 'masuk']
['astaga', 'main', 'aplikasi', 'investasi', 'cocok', 'topup', 'masuk', 'saldonya', 'udah', 'komplain', 'responya', 'lambat', 'beut', 'customer', 'care', 'nol']
['males', 'mengunakan', 'aplikasi', 'dibuka', 'login', 'lelah']
[]
['ribet', 'gunainya']
['lengkapi', 'data', 'ambil', 'foto', 'ktp', 'pencet', 'tanda', 'centang', 'foto']
['isi', 'ul

In [15]:
# Inisialisasi objek stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()

# Mendapatkan data dari koleksi MongoDB
cursor = prepo_collection.find()

for document in cursor:
    filtered_review = document['filtered_review']
    
    # Melakukan stemming pada setiap kata dalam filtered_review
    stemmed_review = [stemmer.stem(word) for word in filtered_review]
    
    # Memperbarui field 'stemmed_review' dengan hasil stemming
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'stemmed_review': stemmed_review}}
    )

    print (stemmed_review)

['verifikasi', 'jelek']
['gagal', 'tanda', 'tangan', 'coba', 'ulang', 'foto', 'ktp', 'foto', 'ktp']
['selesai', 'verifikasi', 'kecewa', 'aplikasi', 'burik']
['cocok', 'jual', 'saham']
['aplikasi', 'ganguan', 'sisa', 'jual', 'saham', 'cocok', 'barusan', 'lihat', 'saham', 'ilang', 'riwayat', 'beli', 'saham', 'investasi', 'td', 'aktif', 'beli', 'saham', 'konfirmasi', 'saham', 'ilang', 'orang', 'uang', 'segitu', 'uang', 'segitu', 'beli', 'kumpul', 'uang', 'kecewa', 'asli']
['tolong', 'baik', 'saham', 'hilang', 'kembali', 'dana']
['ruang', 'email', 'adu', 'jam', 'kerja', 'konfirmasi', 'deposit', 'rdn', 'masuk']
['astaga', 'main', 'aplikasi', 'investasi', 'cocok', 'topup', 'masuk', 'saldo', 'udah', 'komplain', 'responya', 'lambat', 'beut', 'customer', 'care', 'nol']
['males', 'mengunakan', 'aplikasi', 'buka', 'login', 'lelah']
[]
['ribet', 'guna']
['lengkap', 'data', 'ambil', 'foto', 'ktp', 'pencet', 'tanda', 'centang', 'foto']
['isi', 'ulang', 'data', 'muter', 'anjir']
['tolong', 'tambah', 

In [16]:
# Mendapatkan data dari koleksi MongoDB
cursor = prepo_collection.find()

for document in cursor:
    stemmed_review = document['stemmed_review']
    
    # Mengubah array kata hasil stemming menjadi string
    data_clean = ' '.join(stemmed_review)
    
    # Memperbarui field 'data_clean' dengan hasil yang sudah diubah
    prepo_collection.update_one(
        {'_id': document['_id']},
        {'$set': {'data_clean': data_clean}}
    )

    print (data_clean)

verifikasi jelek
gagal tanda tangan coba ulang foto ktp foto ktp
selesai verifikasi kecewa aplikasi burik
cocok jual saham
aplikasi ganguan sisa jual saham cocok barusan lihat saham ilang riwayat beli saham investasi td aktif beli saham konfirmasi saham ilang orang uang segitu uang segitu beli kumpul uang kecewa asli
tolong baik saham hilang kembali dana
ruang email adu jam kerja konfirmasi deposit rdn masuk
astaga main aplikasi investasi cocok topup masuk saldo udah komplain responya lambat beut customer care nol
males mengunakan aplikasi buka login lelah

ribet guna
lengkap data ambil foto ktp pencet tanda centang foto
isi ulang data muter anjir
tolong tambah fitur ganti handphone
eror jam bursa
daftar hasil rumit
aplikasi buruk wd ado mas mohon baik rugi penguna
aktif aktif daftar badut
verifikasi ulang data
kirim kucing depo haya robot sistem malas deposit
aplikasi investasi rekomendasi jual aset jual aset aplikasi aplikasi kerja sabtu mingu libur jam kerja jam pagi jam istirahat j

In [17]:
# Mengecek dan menghapus dokumen dengan field "data_clean" yang kosong
query = {'data_clean': {'$exists': True, '$eq': ''}}
result = prepo_collection.delete_many(query)
print(f"Jumlah dokumen yang dihapus: {result.deleted_count}")

Jumlah dokumen yang dihapus: 192


In [18]:
# Pipeline untuk menghilangkan data duplikat berdasarkan field "data_clean"
pipeline = [
    {
        '$group': {
            '_id': '$data_clean',
            'uniqueIds': {'$addToSet': '$_id'},
            'count': {'$sum': 1}
        }
    },
    {
        '$match': {
            'count': {'$gt': 1}
        }
    }
]

# Eksekusi pipeline
duplicates = list(prepo_collection.aggregate(pipeline))

# Menghapus data duplikat
total_duplicates_removed = 0
for duplicate in duplicates:
    review_ids_to_remove = duplicate['uniqueIds'][1:]
    result = prepo_collection.delete_many({'_id': {'$in': review_ids_to_remove}})
    duplicates_removed_count = result.deleted_count
    total_duplicates_removed += duplicates_removed_count

print('Jumlah data duplikat yang dihapus:', total_duplicates_removed)


Jumlah data duplikat yang dihapus: 923


In [19]:
cursor = prepo_collection.find()
df_ajaib= pd.DataFrame(list(cursor))
df_ajaib

_id  \
0     663862c1dd520c9ba22efdc2   
1     663862c1dd520c9ba22efdc3   
2     663862c1dd520c9ba22efdc4   
3     663862c1dd520c9ba22efdc5   
4     663862c1dd520c9ba22efdc6   
...                        ...   
8627  663a4aee22061f845eb78b6c   
8628  663a4aee22061f845eb78b6d   
8629  663a4aee22061f845eb78b6e   
8630  663a4aee22061f845eb78b70   
8631  663a4aee22061f845eb78b71   

                                                content                  at  \
0                           tidak bisa verifikasi jelek 2024-05-05 12:11:55   
1     selalu gagal dalam tanda tangan coba ulangi fo... 2024-05-05 07:32:30   
2     lama sangat selesai verifikasi nya sangat meng... 2024-05-05 06:58:43   
3     kenapa cocok jual saham selalu tidak bisa bisa ya 2024-05-04 16:24:09   
4     aplikasi tidak tahu lagi ganguan tidak tahu ap... 2024-05-04 05:10:50   
...                                                 ...                 ...   
8627  maf kak kenapa saya tidak bisa menarik dana da... 2021-12-02 17:27:44   
8628                         sangat membantu dan nyaman 2021-12-02 16:09:06   
8629                                 kenapa eroro kakak 2021-12-02 15:21:33   
8630  hai kak bisa bantu saya saya tadi baru aplikas... 2021-12-02 14:37:57   
8631  saya pemula aplikasi ini cukup menjanjikan ses... 2021-12-01 21:15:58   

                                       tokenized_review  \
0                      [tidak, bisa, verifikasi, jelek]   
1     [selalu, gagal, dalam, tanda, tangan, coba, ul...   
2     [lama, sangat, selesai, verifikasi, nya, sanga...   
3     [kenapa, cocok, jual, saham, selalu, tidak, bi...   
4     [aplikasi, tidak, tahu, lagi, ganguan, tidak, ...   
...                                                 ...   
8627  [maf, kak, kenapa, saya, tidak, bisa, menarik,...   
8628                    [sangat, membantu, dan, nyaman]   
8629                             [kenapa, eroro, kakak]   
8630  [hai, kak, bisa, bantu, saya, saya, tadi, baru...   
8631  [saya, pemula, aplikasi, ini, cukup, menjanjik...   

                                        filtered_review  \
0                                   [verifikasi, jelek]   
1     [gagal, tanda, tangan, coba, ulangi, foto, ktp...   
2     [selesai, verifikasi, mengecewakan, aplikasi, ...   
3                                  [cocok, jual, saham]   
4     [aplikasi, ganguan, sisa, penjualan, saham, co...   
...                                                 ...   
8627  [maf, menarik, dana, saldo, rdn, cba, berkali,...   
8628                                 [membantu, nyaman]   
8629                                     [eroro, kakak]   
8630           [bantu, aplikasi, ajaibtpi, login, akun]   
8631  [pemula, aplikasi, menjanjikan, pemula, bantu,...   

                                         stemmed_review  \
0                                   [verifikasi, jelek]   
1     [gagal, tanda, tangan, coba, ulang, foto, ktp,...   
2        [selesai, verifikasi, kecewa, aplikasi, burik]   
3                                  [cocok, jual, saham]   
4     [aplikasi, ganguan, sisa, jual, saham, cocok, ...   
...                                                 ...   
8627   [maf, tarik, dana, saldo, rdn, cba, kali, salah]   
8628                                    [bantu, nyaman]   
8629                                     [eroro, kakak]   
8630           [bantu, aplikasi, ajaibtpi, login, akun]   
8631  [mula, aplikasi, janji, mula, bantu, ayo, kode...   

                                             data_clean  
0                                      verifikasi jelek  
1       gagal tanda tangan coba ulang foto ktp foto ktp  
2              selesai verifikasi kecewa aplikasi burik  
3                                      cocok jual saham  
4     aplikasi ganguan sisa jual saham cocok barusan...  
...                                                 ...  
8627            maf tarik dana saldo rdn cba kali salah  
8628                                       bantu nyaman  
8629                

In [20]:
# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data'] 
prepo_collection = db['02. prepo_data_ajaib']  
clean_collection = db['03. clean_data_ajaib'] 

# Mengambil beberapa dokumen dari koleksi lama
data = prepo_collection.find({}) 

# Menyimpan dokumen-dokumen tersebut ke dalam list
data_list = list(data)

# Menyimpan data ke dalam koleksi baru
clean_collection.insert_many(data_list)


InsertManyResult([ObjectId('663862c1dd520c9ba22efdc2'), ObjectId('663862c1dd520c9ba22efdc3'), ObjectId('663862c1dd520c9ba22efdc4'), ObjectId('663862c1dd520c9ba22efdc5'), ObjectId('663862c1dd520c9ba22efdc6'), ObjectId('663862c1dd520c9ba22efdc7'), ObjectId('663862c1dd520c9ba22efdc8'), ObjectId('663862c1dd520c9ba22efdc9'), ObjectId('663862c1dd520c9ba22efdca'), ObjectId('663862c1dd520c9ba22efdcc'), ObjectId('663862c1dd520c9ba22efdcd'), ObjectId('663862c1dd520c9ba22efdce'), ObjectId('663862c1dd520c9ba22efdcf'), ObjectId('663862c1dd520c9ba22efdd1'), ObjectId('663862c1dd520c9ba22efdd2'), ObjectId('663862c1dd520c9ba22efdd3'), ObjectId('663862c1dd520c9ba22efdd4'), ObjectId('663862c1dd520c9ba22efdd5'), ObjectId('663862c1dd520c9ba22efdd6'), ObjectId('663862c1dd520c9ba22efdd7'), ObjectId('663862c1dd520c9ba22efdd8'), ObjectId('663862c1dd520c9ba22efdd9'), ObjectId('663862c1dd520c9ba22efdda'), ObjectId('663862c1dd520c9ba22efddb'), ObjectId('663862c1dd520c9ba22efddc'), ObjectId('663862c1dd520c9ba22efd

In [21]:
# Menghapus field yang tidak diperlukan
clean_collection.update_many({}, {'$unset': {'tokenized_review': '', 'filtered_review': '', 'stemmed_review': '', 'content': ''}})

# Menampilkan data setelah penghapusan field
cursor = clean_collection.find()
for document in cursor:
    print(document)

{'_id': ObjectId('663862c1dd520c9ba22efdc2'), 'at': datetime.datetime(2024, 5, 5, 12, 11, 55), 'data_clean': 'verifikasi jelek'}
{'_id': ObjectId('663862c1dd520c9ba22efdc3'), 'at': datetime.datetime(2024, 5, 5, 7, 32, 30), 'data_clean': 'gagal tanda tangan coba ulang foto ktp foto ktp'}
{'_id': ObjectId('663862c1dd520c9ba22efdc4'), 'at': datetime.datetime(2024, 5, 5, 6, 58, 43), 'data_clean': 'selesai verifikasi kecewa aplikasi burik'}
{'_id': ObjectId('663862c1dd520c9ba22efdc5'), 'at': datetime.datetime(2024, 5, 4, 16, 24, 9), 'data_clean': 'cocok jual saham'}
{'_id': ObjectId('663862c1dd520c9ba22efdc6'), 'at': datetime.datetime(2024, 5, 4, 5, 10, 50), 'data_clean': 'aplikasi ganguan sisa jual saham cocok barusan lihat saham ilang riwayat beli saham investasi td aktif beli saham konfirmasi saham ilang orang uang segitu uang segitu beli kumpul uang kecewa asli'}
{'_id': ObjectId('663862c1dd520c9ba22efdc7'), 'at': datetime.datetime(2024, 5, 3, 23, 3, 50), 'data_clean': 'tolong baik saha

In [22]:
clean_collection.update_many(
    {},
    {
        '$set': {
            'label': None
        }
    }
)

UpdateResult({'n': 8632, 'nModified': 8632, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [23]:
client.close()